## Event Search Example 2

### Example code to search for occultations from chosen sites

Revisions:

    2023 Jun 12 - rfrench - original version


In [74]:
from astropy.table import Table
from astropy.time import Time
import numpy as np
import os
import glob

program  = 'EventSearchExample2.py'

# Modify this line to point to the path to the local copy of the SOM directory 
# Be sure to include the trailing slash /

# This is the correct SOM_path if the program is run in its default path:
# SOM/doc/EventSearchExample1.py

SOM_path = '../'
OutputFile  = 'EventSearchExample2.out'
    
# Example 2 
#
# run options:
#    ListSummaryFiles 
#       (=True to list the names of summary pdf files for identified events)
#    ListEventFiles 
#       (=True to list the names of site-specific event details for identified events)
#    OpenSummaryFiles 
#       (=True to use OS command to display summary pdf files for identified events)
#    DisplayOutputFile 
#       (=True to display contents of output file with results of search)
#    DetailedOutput = True to include detailed output in the output file
#       includes list of quantities available in data table from Machine Readable file
#       includes listing of Event files if ListEventFiles is True
#    verbose
#        (=True for intermediate progress reports)
# 
# event search specifications:
# Find all predicted occultations by selected
#    Targets
# with corresponding K magnitude upper limits
#    Kmaglims
# visible between specified dates
#    UTCmin, UTCmax
# from sites chosen from list of AvailableSites
#    RequestedSites

ListSummaryFiles = True # set to False to suppress listing of summary pdf
ListEventFiles = True # set to False to suppress listing of individual detailed event files
OpenSummaryFiles = True # set to True if "open *.pdf" is a legal OS command
DisplayOutputFile = True # set to False to suppress display of contents of output file
DetailedOutput = True # quantities available in data table from Machine Readable file, event files
verbose = True # if True, then provde intermediate reports on the search

# specify list of targets to search

Targets = ['Jupiter','Saturn','Uranus','Neptune','Titan','Triton']

# specify corresponding upper limits on K magnitude

Kmaglims = [5, 8, 10.9, 11, 7, 15]

# specify date range for search (between 2023-01-01 and 2050-01-01)

UTCmin = '2024-01-01'
UTCmax = '2030-01-01'


AvailableSites = ['PIC','PAL','PMO','KPNO','MCD','TEN','IRTF',\
        'KAV','RIO','ESO','AAT','SAAO','MSO']
SiteNames = ['Pic du Midi','Palomar','Purple Mountain','Kitt Peak',\
            'McDonald','Tenerife','Mauna Kea','Kavalur','Rio di Janeiro'\
            'Eur. S. Obs','Anglo-Aus tel.','South Afr. Astr. Obs',\
            'Mt. Stromlo']
SiteRegions = ['ENA','NAM','EAS','NAM','NAM','ENA','NAM','EAS',\
              'SAM','SAM','OCN','SAF','OCN']

# specify sites to use from above list
SelectedSites = ['IRTF','TEN','KPNO']

# END OF USER INPUT

# list of available region codes and abbreviated names

RegionCodes = ['NAM','ENA','SAF','SAM','OCN','EAS']
RegionNames = \
 ['N. Am.','Eur.&N.Afr.','S. Afr.','S. Am.','Oceania','E. Asia']

# Determine which regions to use for this search

RequestedRegions= [False,False,False,False,False,False]

for SelectedSite in SelectedSites:
    index = AvailableSites.index(SelectedSite)
    SiteRegion = SiteRegions[index]
    index = RegionCodes.index(SiteRegion)
    RequestedRegions[index]=True

f = open(OutputFile, 'w')
print("Results of ",program,file=f)

count = 0
for SelectedSite in SelectedSites:
    if count == 0 :
        Sitelist = SelectedSite
    else:
        Sitelist = Sitelist + ', '+SelectedSite
    count = count + 1

# convert from requested date range to Julian dates

JDmin = Time(UTCmin,format='iso',scale='utc').jd
JDmax = Time(UTCmax,format='iso',scale='utc').jd

# for each target...
first = True
for Target,Kmaglim in (zip(Targets,Kmaglims)):
    inMRfile = SOM_path+'tables/' +Target+'/'+Target+'_predictions_MR.txt'
    data = Table.read(inMRfile, format="ascii.cds")

    if verbose and first:
        print('Available contents of data array from MR file:',file=f)
        print(data.info,file=f)
        first = False

        # search for requested events...

    Lmatch = np.where((data['JD'] >= JDmin) & (data['JD'] <= JDmax)
                 & (data['KMAG']<=Kmaglim))

    # determine if ring event is visible from a given region

    print("------------------------------------------------------------------------------",file=f)
    print("Results of search for occultations by",Target,"between",UTCmin,"and",UTCmax,file=f)
    print("K magnitude limit",Kmaglim,file=f)
    print('Visible from ',Sitelist,file=f)
    print(' ',file=f)

    data_ = data[Lmatch]
    total = 0
    for i in range(len(data_)):
        data_i = data_[i]
        visible = ''
        count = 0
        EventFiles= []
        for RequestedRegion,RegionCode,RegionName in \
            zip(RequestedRegions,RegionCodes,RegionNames):
            if RequestedRegion is False:
                continue
        # confirm that a ring or planet event is visible from this region
            if (data_i[RegionCode+'_N_RINGOCCS'] == 0) and (data_i[RegionCode+'_N_TARGETOCCS']==0):
                continue  
        # search for detailed file for requested sites
            if verbose:
                print('SelectedSites=',SelectedSites)
            for SelectedSite in SelectedSites:
                index = AvailableSites.index(SelectedSite)
                SiteRegion = SiteRegions[index]
                if RegionCode != SiteRegion:
                    if verbose:
                        print(SelectedSite,'is not in',RegionCode)
                    continue
                else:
                    if verbose:
                        print(SelectedSite,'is in',RegionCode)
                    EventSummaryFile = SOM_path + data_i['SUMMARY_PDF'][4:]
                    esf=EventSummaryFile
                    search_string = esf[0:len(esf)-len('_20230528a.pdf')+1]+SelectedSite+'*.txt'
                    if verbose:
                        print('Search string:',search_string)
                    EventDetailsFileList = glob.glob(search_string)
                    if len(EventDetailsFileList) == 0:
                        if verbose:
                            print('No matching file found... skipping')
                        continue
                    if verbose:
                        print('EventDetailsFile =',EventDetailsFileList[0])
                    EventFiles.append(EventDetailsFileList[0])
                if count >0:
                    char=', '
                else:
                    char=''
                visible = visible+char+SelectedSite 
                count = count + 1
                total = total + 1
    # An event has been found. List and/or open the summary file if requested
                if count == 1 and (ListSummaryFiles or OpenSummaryFiles):
                    EventSummaryFile = SOM_path + data_i['SUMMARY_PDF'][4:]
                    if OpenSummaryFiles:
                        command = 'open '+EventSummaryFile
                        os.system(command)                 
        if count >0:
                print('  '+data_i['UTC_CA'],f'{data_i["EVENTTYPE"]:<{7}}',\
                      'K=',data_i['KMAG'],'is visible from',visible,file=f)

                if ListSummaryFiles:
                    print(' ',file=f)
                    print('  Event summary file:',file=f)
                    print(EventSummaryFile,file=f) 
                    print(' ',file=f)
                if ListEventFiles:
                    print('  Detailed event files:',file=f)
                    for EventFile in  EventFiles:
                        print(EventFile,file=f) 
                        print(' ',file=f)
                        if DetailedOutput:
                            with open(EventFile) as ff:
                                contents = ff.read()
                                print(contents,file=f)                      
    if total == 0:
        print('No events found with requested conditions',file=f)
    print(" ",file=f)
f.close()
if DisplayOutputFile:
    print('********** Contents of ',OutputFile,' ****************')
    with open(OutputFile) as f:
        contents = f.read()
        print(contents)

SelectedSites= ['IRTF', 'TEN', 'KPNO']
IRTF is in NAM
Search string: ../events/Jupiter/2027/Jupiter_2027-02-22T11_12_09.020_IRTF*.txt
EventDetailsFile = ../events/Jupiter/2027/Jupiter_2027-02-22T11_12_09.020_IRTF_20230528a.txt
TEN is not in NAM
KPNO is in NAM
Search string: ../events/Jupiter/2027/Jupiter_2027-02-22T11_12_09.020_KPNO*.txt
EventDetailsFile = ../events/Jupiter/2027/Jupiter_2027-02-22T11_12_09.020_KPNO_20230528a.txt
SelectedSites= ['IRTF', 'TEN', 'KPNO']
IRTF is in NAM
Search string: ../events/Saturn/2024/Saturn_2024-08-06T17_12_21.220_IRTF*.txt
EventDetailsFile = ../events/Saturn/2024/Saturn_2024-08-06T17_12_21.220_IRTF_20230528a.txt
TEN is not in NAM
KPNO is in NAM
Search string: ../events/Saturn/2024/Saturn_2024-08-06T17_12_21.220_KPNO*.txt
No matching file found... skipping
SelectedSites= ['IRTF', 'TEN', 'KPNO']
IRTF is not in ENA
TEN is in ENA
Search string: ../events/Saturn/2029/Saturn_2029-07-19T00_57_19.090_TEN*.txt
EventDetailsFile = ../events/Saturn/2029/Saturn_2